In [21]:
import os
import pandas as pd
from Plot import Plot
import numpy as np
import pandas_ta as ta
import numpy as np
from datetime import datetime
import time
import sys

In [15]:
data_file = 'BTC_15'
number = 1
opti_ratio = 0.75
riskRatio = 1.5
slowLen = 5
fastLen = 18
trend1 = 50
trend2 = 89
trend3 = 144
midLen = 35
lowerLen = 35
c = 45/100

In [ ]:
def RandS(data_file,number,opt_ratio):
    data_list=[]
    name=data_file[0:3]
    header = ['Timestamp', 'Open', 'High', 'Low', 'Close']
    for file in os.listdir(data_file):
        if file.endswith('.csv'):
            data_list.append(file)
    for file in data_list:
        if str(number) in file:
            file_string = data_file+'/'+name+str(number)+'.csv'
            df = pd.read_csv(file_string)
            sample_length = len(df)
            in_sample_length = round(sample_length*opt_ratio)
            in_sample = pd.read_csv(file_string,nrows=in_sample_length)
            out_of_sample = pd.read_csv(file_string,names=header,skiprows=in_sample_length)
    return in_sample, out_of_sample

In [ ]:
def opt_Analysis(df, riskRatio, slowLen,  fastLen, trend1, trend2, trend3, midLen, lowerLen, c):
    print('Optimising...')
    df['a'] = abs(df.apply(lambda row: row.High - row.Low, axis=1))
    df['b'] = abs(df.apply(lambda row: row.Close - row.Open, axis=1))
    df['ca'] = df.apply(lambda row: row.a * c, axis=1)
    df['rv'] = np.where(df['b'].values < df['ca'].values,1,0)
    df['x'] = df.apply(lambda row: row.Low + row.ca, axis=1)
    df['y'] = df.apply(lambda row: row.High - row.ca, axis=1)
    df['sl'] = np.where((df['High'].values>df['y'].values) & (df['Close'].values<df['y'].values) & (df['Open'].values<df['y'].values),1,0)
    df['ss'] = np.where((df['Low'].values<df['x'].values) & (df['Close'].values>df['x'].values) & (df['Open'].values>df['x'].values),1,0)
    df['longlimit'] = np.where((df['sl'] > 0), df['High'].values,np.NaN)
    df['longlimit'] = df['longlimit'].ffill()
    df['longlimit'] = np.array(df['longlimit']).tolist()
    df['shortlimit'] = np.where((df['ss'] > 0), df['Low'].values,np.NaN)
    df['shortlimit'] = df['shortlimit'].ffill()
    df['shortlimit'] = np.array(df['shortlimit']).tolist()
    df['hc'] = df.High - df.Low
    df['hcs'] = abs(df.High-df.Close.shift(1))
    df['lcs'] = abs(df.Low-df.Close.shift(1))
    df['rt'] = df[['hc','hcs','lcs']].max(axis=1)
    df['slow'] = ta.sma(df['Close'],slowLen)
    df['fast'] = ta.ema(df['Close'],fastLen)
    df['trend 1'] = ta.sma(df['Close'],trend1)
    df['trend 2'] = ta.sma(df['Close'],trend2)
    df['trend 3'] = ta.ema(df['Close'],trend3)
    df['mid'] = ta.ema(df['Close'],midLen)
    df['lower'] = ta.ema(df['Close'],lowerLen) + 0.5*(ta.rma(df['rt'],lowerLen))
    df['longOn'] = np.where((df.slow.values>df.fast.values)&(df['trend 1'].values<df.fast.values)&(df['trend 2'].values<df.fast.values)&(df['trend 3'].values<df.fast.values)&(df['mid'].values<df.fast.values)&(df['lower'].values<df.fast.values),'y','n')
    df['shortOn'] = np.where((df.slow.values<df.fast.values)&(df['trend 1'].values>df.fast.values)&(df['trend 2'].values>df.fast.values)&(df['trend 3'].values>df.fast.values)&(df['mid'].values>df.fast.values)&(df['lower'].values>df.fast.values),'y','n')
    df['longstop'] = np.where((df['slow'].values>df['Low'].values),df['fast'].values,df['slow'].values)
    df['shortstop'] = np.where((df['slow'].values<df['High'].values),df['fast'].values,df['slow'].values)
    df['longtarget'] = df.apply(lambda row: abs((row.longstop / row.longlimit) - 1)*riskRatio, axis=1)
    df['longtarget'] = df.apply(lambda row: (row.longlimit * (row.longtarget + 1)), axis=1)
    df['shorttarget'] = df.apply(lambda row: abs((row.shortstop / row.shortlimit) - 1)*riskRatio, axis=1)
    df['shorttarget'] = df.apply(lambda row: (row.shortlimit * (1 - row.shorttarget)), axis=1)
    pd.set_option('display.max_rows', df.shape[0]+1)
    pd.set_option('display.max_columns',df.shape[0]+1)
    return df

In [13]:
def optimise(data_file, number, opti_ratio, riskRatio, slowLen,  fastLen, trend1, trend2, trend3, midLen, lowerLen, c):
    df = recallNum(data_file,number)
    splitIndex = round(opti_ratio*len(df))
    in_sample = df.head(splitIndex)
    in_sample = optimiseAnalysis(in_sample, riskRatio, slowLen,  fastLen, trend1, trend2, trend3, midLen, lowerLen, c)
    return in_sample

In [22]:
optimise(data_file, number, opti_ratio, riskRatio, slowLen, fastLen, trend1, trend2, trend3, midLen, lowerLen, c)

Optimising...


/srv/conda/envs/notebook/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/srv/conda/envs/notebook/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
/srv/conda/envs/notebook/lib/python3.7/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a 

Timestamp      Open      High       Low     Close       a  \
0     2019-07-20 12:30:00  10564.25  10573.25  10550.25  10556.50   23.00   
1     2019-07-20 12:45:00  10556.50  10568.00  10525.50  10539.50   42.50   
2     2019-07-20 13:00:00  10539.50  10568.25  10521.00  10568.25   47.25   
3     2019-07-20 13:15:00  10588.50  10796.25  10557.00  10583.00  239.25   
4     2019-07-20 13:30:00  10583.00  10589.50  10477.00  10552.00  112.50   
5     2019-07-20 13:45:00  10552.00  10575.50  10528.00  10548.75   47.50   
6     2019-07-20 14:00:00  10548.75  10582.00  10548.75  10572.25   33.25   
7     2019-07-20 14:15:00  10572.25  10601.25  10554.25  10588.00   47.00   
8     2019-07-20 14:30:00  10588.00  10612.75  10576.75  10608.50   36.00   
9     2019-07-20 14:45:00  10608.50  10628.25  10600.75  10621.25   27.50   
10    2019-07-20 15:00:00  10621.25  10623.50  10593.00  10593.25   30.50   
11    2019-07-20 15:15:00  10593.25  10618.25  10579.75  10607.25   38.50   
12    2019-07-20 15:30:00  10607.25  10675.75  10594.00  10613.50   81.75   
13    2019-07-20 15:45:00  10613.50  10657.50  10601.50  10647.50   56.00   
14    2019-07-20 16:00:00  10644.25  10700.00  10608.75  10625.50   91.25   
15    2019-07-20 16:15:00  10626.25  10702.75  10626.25  10674.00   76.50   
16    2019-07-20 16:30:00  10674.00  10726.00  10667.50  10721.25   58.50   
17    2019-07-20 16:45:00  10721.25  10881.75  10691.00  10821.00  190.75   
18    2019-07-20 17:00:00  10826.75  11053.25  10816.25  10925.00  237.00   
19    2019-07-20 17:15:00  10925.00  10988.00  10902.00  10935.75   86.00   
20    2019-07-20 17:30:00  10935.75  10965.50  10872.75  10890.00   92.75   
21    2019-07-20 17:45:00  10890.00  10931.75  10880.25  10913.50   51.50   
22    2019-07-20 18:00:00  10912.75  10947.25  10911.50  10945.00   35.75   
23    2019-07-20 18:15:00  10945.00  10960.75  10924.75  10928.00   36.00   
24    2019-07-20 18:30:00  10928.00  10973.00  10927.25  10956.75   45.75   
25    2019-07-20 18:45:00  10956.75  10967.75  10936.50  10941.25   31.25   
26    2019-07-20 19:00:00  10941.25  10944.75  10904.50  10918.75   40.25   
27    2019-07-20 19:15:00  10918.75  10933.75  10900.75  10918.25   33.00   
28    2019-07-20 19:30:00  10918.25  10944.00  10894.25  10922.75   49.75   
29    2019-07-20 19:45:00  10922.75  10946.50  10910.75  10931.75   35.75   
30    2019-07-20 20:00:00  10931.75  10960.00  10925.50  10925.50   34.50   
31    2019-07-20 20:15:00  10925.50  10963.25  10916.25  10921.75   47.00   
32    2019-07-20 20:30:00  10921.75  10932.50  10908.25  10924.00   24.25   
33    2019-07-20 20:45:00  10924.00  10941.25  10909.75  10941.25   31.50   
34    2019-07-20 21:00:00  10941.25  10945.00  10907.50  10910.25   37.50   
35    2019-07-20 21:15:00  10910.25  10940.00  10910.25  10940.00   29.75   
36    2019-07-20 21:30:00  10940.00  10953.75  10932.50  10953.75   21.25   
37    2019-07-20 21:45:00  10953.75  10966.25  10945.00  10966.25   21.25   
38    2019-07-20 22:00:00  10966.25  10988.75  10949.75  10951.75   39.00   
39    2019-07-20 22:15:00  10951.75  10972.25  10942.75  10972.25   29.50   
40    2019-07-20 22:30:00  10972.25  10983.25  10954.00  10983.25   29.25   
41    2019-07-20 22:45:00  10983.25  11016.50  10971.75  11011.75   44.75   
42    2019-07-20 23:00:00  11011.75  11108.75  11003.25  11040.75  105.50   
43    2019-07-20 23:15:00  11040.75  11051.25  10946.25  10973.25  105.00   
44    2019-07-20 23:30:00  10973.25  10988.50  10843.00  10843.00  145.50   
45    2019-07-20 23:45:00  10843.00  10843.00  10625.75  10765.75  217.25   
46    2019-07-21 00:00:00  10765.75  10772.75  10672.75  10772.00  100.00   
47    2019-07-21 00:15:00  10772.00  10804.50  10761.00  10781.25   43.50   
48    2019-07-21 00:30:00  10780.50  10834.00  10779.50  10825.25   54.50   
49    2019-07-21 00:45:00  10825.25  10828.25  10777.50  10801.50   50.75   
50    2019-07-21 01:00:00  10800.75  10825.50  10787.00  10823.25   38.50   
51    2019-0